# Homework 1 (Total Points: 175)



Learning Goals:
- Learn how to load a dataset and process it.
- Learn how to implement several IR methods (TFIDF, BM25, QL) and understand their weaknesses & strengths.
- Learn how to evaluate IR methods


**NOTE 1**: Only the code (`TODO: Implement this!` denotes these sections) is graded. The 'theory' questions in this assignment serve as a preparation for the exam and to facilitate a deeper understanding of the course content. These questions (denoted by `TODO: Answer this!`) have no points assigned to them, but **need** to be filled out before submission.  

**NOTE 2**: You can use the `nltk`, `numpy` and `matplotlib` libraries here. Other libraries, e.g., `gensim` or `scikit-learn`, may not be used. 

**NOTE 3**: The notebook you submit has to have the student ids, seperated by underscores (E.g., `12341234_12341234_12341234.ipynb`). 

**NOTE 4**: Make sure to check that your notebook runs before submission. A quick way to do this is to restart the kernel and run all the cells.  

---
Additional Resources: 
-  Sections 2.3, 4.1, 4.2, 4.3, 5.3, 5.6, 5.7, 6.2, 7, 8 of [Search Engines: Information Retrieval in Practice](https://ciir.cs.umass.edu/downloads/SEIRiP.pdf)


In [29]:
# !pip3 install nltk
# !pip3 install tqdm

In [30]:
# imports 
# TODO: Ensure that no additional library is imported in the notebook. 
# TODO: Only the standard library and the following libraries are allowed:

import os
import zipfile
from functools import partial

import nltk
import requests
import numpy as np
from tqdm import tqdm
import heapq

import matplotlib.pyplot as plt

from ipywidgets import widgets
from IPython.display import display, HTML
from IPython.html import widgets
from collections import namedtuple
from collections import Counter
from pprint import pprint

%matplotlib inline

## Section 1: Text Processing (20 points)

In this section, we will load the dataset and learn how to clean up the data to make it usable for an IR system. 

We are using the [CACM dataset](http://ir.dcs.gla.ac.uk/resources/test_collections/cacm/), which is a small, classic IR dataset, composed of a collection of titles and abstracts from the journal CACM. It comes with relevance judgements for queries, so we can evaluate our IR system. 

The following cell downloads the dataset and unzips it to a local directory

In [31]:
def download_dataset(folder_path = "./datasets/"):
    
    os.makedirs(folder_path, exist_ok=True)
    
    file_location = os.path.join(folder_path, "cacm.zip")
    
    # download file if it doesn't exist
    if not os.path.exists(file_location):
        
        url = "https://surfdrive.surf.nl/files/index.php/s/M0FGJpX2p8wDwxR/download"

        with open(file_location, "wb") as handle:
            print(f"Downloading file from {url} to {file_location}")
            response = requests.get(url, stream=True)
            for data in tqdm(response.iter_content()):
                handle.write(data)
            print("Finished downloading file")
    
    if not os.path.exists(os.path.join(folder_path, "train.txt")):
        
        # unzip file
        with zipfile.ZipFile(file_location, 'r') as zip_ref:
            zip_ref.extractall(folder_path)
        
download_dataset()

You can see a brief description of each file in the dataset by looking at the README file

In [32]:
##### Read the README file 
!cat ./datasets/README
#####

Files in this directory with sizes:
          0 Jun 19 21:01 README

    2187734 Jun 19 20:55 cacm.all              text of documents
        626 Jun 19 20:58 cite.info             key to citation info
                                                (the X sections in cacm.all)
       2668 Jun 19 20:55 common_words           stop words used by smart
       2194 Jun 19 20:55 make_coll*             shell script to make collection
       1557 Jun 19 20:55 make_coll_term*        ditto (both useless without
                                                smart system)
       9948 Jun 19 20:55 qrels.text             relation giving
                                                    qid did 0 0
                                                to indicate dument did is
                                                relevant to query qid
      13689 Jun 19 20:55 query.text             Original text of the query


----
We are interested in 4 files:
- `cacm.all` : Contains the text for all documents. Note that some documents do not have abstracts available. 
- `query.text` : The text of all queries
- `qrels.text` : The relevance judgements
- `common_words` : A list of common words. This may be used as a collection of stopwords

In [33]:
##### The first 45 lines of the CACM dataset forms the first record
# We are interested only in 3 fields. 
# 1. the '.I' field, which is the document id
# 2. the '.T' field (the title) and
# 3. the '.W' field (the abstract, which may be absent)
!head -45 ./datasets/cacm.all
#####

.I 1
.T
Preliminary Report-International Algebraic Language
.B
CACM December, 1958
.A
Perlis, A. J.
Samelson,K.
.N
CA581203 JB March 22, 1978  8:28 PM
.X
100	5	1
123	5	1
164	5	1
1	5	1
1	5	1
1	5	1
205	5	1
210	5	1
214	5	1
1982	5	1
398	5	1
642	5	1
669	5	1
1	6	1
1	6	1
1	6	1
1	6	1
1	6	1
1	6	1
1	6	1
1	6	1
1	6	1
1	6	1
165	6	1
196	6	1
196	6	1
1273	6	1
1883	6	1
324	6	1
43	6	1
53	6	1
91	6	1
410	6	1
3184	6	1


---

Now, write a function to read in the `cacm.all` file. Note that each document has a variable number of lines. The `.I` field denotes a new document

In [34]:
# TODO: Implement this! (4 points)
def read_cacm_docs(root_folder = "./datasets/"):
    """
        Reads in the CACM documents. The dataset is assumed to be in the folder "./datasets/cacm" be default
        Returns: A list of 2-tuples: (doc_id, document), where 'document' is a single string created by 
            appending the title and abstract (seperated by a "\n"). 
            In case the record doesn't have an abstract, the document is composed only by the title
    """
    
    file = root_folder + 'cacm.all'
    cacm_list = []
    with open(file, 'r') as f:
        doc_string = f.read()
        documents = doc_string.split('.I ')
        
        for doc in documents[1:]:
            
            doc = doc.split('\n')
            doc_id = int(doc[0])
            
            for i, line in enumerate(doc):
                
                if line == '.T':
                    title_start = i + 1
                if line == '.W':
                    abstract_start = i + 1
                if line == '.B':
                    abstract_end = i
                    
            try:
                abstract = ' '.join(doc[abstract_start:abstract_end])
                title = ' '.join(doc[title_start:abstract_start-1])
                title_abstract = title + '\n' + abstract
                
            except:
                title = ' '.join(doc[title_start:abstract_end])
                title_abstract = title
            
            cacm_list.append((doc_id, title_abstract))
                
            abstract_start = None
            abstract_end = None
            abstract = None
                
    return cacm_list

docs = read_cacm_docs()
pprint(docs[:50])

[(1, 'Preliminary Report-International Algebraic Language'),
 (2, 'Extraction of Roots by Repeated Subtractions for Digital Computers'),
 (3, 'Techniques Department on Matrix Program Schemes'),
 (4, 'Glossary of Computer Engineering and Programming Terminology'),
 (5, 'Two Square-Root Approximations'),
 (6, 'The Use of Computers in Inspection Procedures'),
 (7, 'Glossary of Computer Engineering and Programming Terminology'),
 (8, 'On The Equivalence and Transformation of Program Schemes'),
 (9, 'Proposal for an UNCOL'),
 (10, 'Glossary of Computer Engineering and Programming Terminology'),
 (11,
  'The Problem of Programming Communication with Changing Machines A Proposed '
  'Solution-Part 2'),
 (12, 'Error Estimation in Runge-Kutta Procedures'),
 (13, 'Glossary of Computer Engineering and Programming Terminology'),
 (14,
  'The Problem of Programming Communication with Changing Machines A Proposed '
  'Solution (Part 1)'),
 (15, 'Recursive Curve Fitting Technique'),
 (16, "Secant Mod

In [35]:
##### 
assert len(docs) == 3204, "There should be exactly 3024 documents"
##### 

---

Next, let us read the queries. They are formatted similarly: 

In [36]:
##### The first 15 lines of 'query.text' has 2 queries
# We are interested only in 2 fields. 
# 1. the '.I' - the query id
# 2. the '.W' - the query
# 3. the '.W' field (the abstract, which may be absent)
!head -15 ./datasets/query.text
#####

.I 1
.W
 What articles exist which deal with TSS (Time Sharing System), an
operating system for IBM computers?
.N
 1. Richard Alexander, Comp Serv, Langmuir Lab (TSS)
 
.I 2
.W
 I am interested in articles written either by Prieve or Udo Pooch
.A
Prieve, B.
Pooch, U.
.N
 2. Richard Alexander, Comp Serv, Langmuir Lab (author = Pooch or Prieve)


---

Now, write a function to read in this file:

In [37]:
# TODO: Implement this! (3 points)
def read_queries(root_folder = "./datasets/"):
    """
        Reads in the CACM queries. The dataset is assumed to be in the folder "./datasets/" be default
        Returns: A list of 2-tuples: (query_id, query)
    """
    
    file = root_folder + 'query.text'
    queries_list = []
    with open(file, 'r') as f:
        doc_string = f.read()
        documents = doc_string.split('.I ')
        documents = [doc for doc in documents if doc != '']
    
        for doc in documents:
            doc = doc.split('\n')
            query_id = int(doc[0])
        
            query_start = None
            query_end = None
            
            for i, line in enumerate(doc):
                
                if line == '.W':
                    query_start = i + 1
                if line == '.A' or line == '.N':
                    if query_end == None:
                        query_end = i
                        
            query = ' '.join(doc[query_start:query_end])
                
            queries_list.append((query_id, query))
    
    return queries_list
                
queries = read_queries()
pprint(queries[:50])

[(1,
  ' What articles exist which deal with TSS (Time Sharing System), an '
  'operating system for IBM computers?'),
 (2, ' I am interested in articles written either by Prieve or Udo Pooch'),
 (3,
  ' Intermediate languages used in construction of multi-targeted compilers; '
  'TCOLL'),
 (4,
  " I'm interested in mechanisms for communicating between disjoint processes, "
  'possibly, but not exclusively, in a distributed environment.  I would '
  'rather see descriptions of complete mechanisms, with or without '
  'implementations, as opposed to theoretical work on the abstract problem.  '
  'Remote procedure calls and message-passing are examples of my interests.'),
 (5,
  " I'd like papers on design and implementation of editing interfaces, "
  'window-managers, command interpreters, etc.  The essential issues are human '
  'interface design, with views on improvements to user efficiency, '
  'effectiveness and satisfaction.'),
 (6,
  ' Interested in articles on robotics, motion p

In [38]:
##### 
assert len(queries) == 64 and all([q[1] is not None for q in queries]), "There should be exactly 64 queries"
##### 

---

Read in the stop words:

In [39]:
!head ./datasets/common_words

a
about
above
accordingly
across
after
afterwards
again
against
all


In [40]:
# TODO: Implement this! (3 points)
def load_stopwords(root_folder = "./datasets/"):
    """
    Load the stopwords
    Output: A set of stopwords
    """
    
    file = root_folder + 'common_words'
    
    with open(file, 'r') as f:
        lines = f.readlines()
        lines_stripped = [line.strip() for line in lines]
        stopwords_set = set(lines_stripped)
    
    return stopwords_set

stopwords = load_stopwords()
assert len(stopwords) == 428

--- 

We can now write some basic text processing functions. A first step is to tokenize the text. You may use any tokenizer available in the `nltk` library:

In [41]:
# TODO: Implement this! (5 points)
def tokenize(text):
    """
        Tokenize the text. 
        Input: text - a string
        Output: a list of tokens
    """
    
    return nltk.word_tokenize(text)

In [42]:
#####
text = "the quick brown fox jumps over the lazy dog"
tokens = tokenize(text)
print(tokens)
#####

['the', 'quick', 'brown', 'fox', 'jumps', 'over', 'the', 'lazy', 'dog']


---

### *Answer the following questions*: 
- Why is stemming necessary, in particular for IR?
    - *TODO: Answer this!*
- Is there any setting (domain, scenario, etc) in which stemming can hurt performance? Illustrate with an example
    - *TODO: Answer this!*

Write a function to stem tokens. Again, you can use the `nltk` library for this

In [43]:
# TODO: Implement this! (5 points)
def stem_token(token):
    """
        Stem the given token, using any stemmer available from the nltk library
        Input: a single token
        Output: the stem of the token
    """
    stemmer = nltk.SnowballStemmer("english")
    return stemmer.stem(token)

In [44]:
####
print([stem_token(t) for t in tokens])
tokens_ = [
    'caresses', 'flies', 'dies', 'mules', 'denied',
    'died', 'agreed', 'owned', 'humbled', 'sized',
    'meeting', 'stating', 'siezing', 'itemization',
    'sensational', 'traditional', 'reference', 'colonizer',
    'plotted']
print([stem_token(t) for t in tokens_])
####

['the', 'quick', 'brown', 'fox', 'jump', 'over', 'the', 'lazi', 'dog']
['caress', 'fli', 'die', 'mule', 'deni', 'die', 'agre', 'own', 'humbl', 'size', 'meet', 'state', 'siez', 'item', 'sensat', 'tradit', 'refer', 'colon', 'plot']


---

### *Answer the following questions*: 
- Another processing step (not done here) is to use n-grams. Illustrate why you would want to use n-grams in IR with an example.  
    - *TODO: Answer this!*
- Usage of n-grams exacerbates some problems ex. in bi-gram language models. What is this problem? Suggest one solution 
    - *TODO: Answer this!*

--- 

The following function puts it all together. Given a string, it tokenizes it, and processes it according to the flags that you set.

In [45]:
#### Putting it all together
def process_text(text, stem=False, remove_stopwords=False, lowercase_text=False):
    
    tokens = []
    for token in tokenize(text):
#         if token.isalpha():    # get rid of punctuation marks and numbers
        if remove_stopwords and token.lower() in stopwords:
            continue
        if stem:
            token = stem_token(token)
        if lowercase_text:
            token = token.lower()
        tokens.append(token)

    return tokens
#### 

Let's create two sets of pre-processed documents

In [46]:
# In this configuration:
# Don't preprocess the text, except to tokenize 
config_1 = {
  "stem": False,
  "remove_stopwords" : False,
  "lowercase_text": True
} 


# In this configuration:
# Preprocess the text: stem and remove stopwords
config_2 = {
  "stem": True,
  "remove_stopwords" : True,
  "lowercase_text": True, 
} 


We can now process the documents and queries according to the configuration specified above

In [47]:
####
doc_repr_1 = []
doc_repr_2 = []
for (doc_id, document) in docs:
    doc_repr_1.append((doc_id, process_text(document, **config_1)))
    doc_repr_2.append((doc_id, process_text(document, **config_2)))

print(len(doc_repr_1))
print(doc_repr_1[60:66])
print(doc_repr_2[:50])

####

3204
[(61, ['ibm', '709', 'tape', 'matrix', 'compiler']), (62, ['multi-dimensional', 'least-squares', 'polynomial', 'curve', 'fitting']), (63, ['octal', 'diagrams', 'of', 'binary', 'conception', 'and', 'their', 'applicability', 'to', 'computer', 'design', 'logic', 'this', 'paper', 'dates', 'back', 'the', 'genesis', 'of', 'binary', 'conception', 'circa', '5000', 'years', 'ago', ',', 'and', 'octal', 'diagrams', 'about', '4800', 'years', 'ago', ',', 'as', 'derived', 'by', 'the', 'chinese', 'ancients', '.', 'it', 'analyzes', 'the', 'applicability', 'of', 'binary', 'trinities', 'of', 'the', 'octal', 'diagrams', 'to', 'modern', 'electronic-digital-computer', 'design', 'logic', '.']), (64, ['remarks', 'on', 'algol', 'and', 'symbol', 'manipulation']), (65, ['algol', 'sub-committee', 'report', '-', 'extensions']), (66, ['a', 'proposal', 'for', 'a', 'generalized', 'card', 'code', 'for', '256', 'characters'])]
[(1, ['preliminari', 'report-intern', 'algebra', 'languag']), (2, ['extract', 'root', '


--- 

## Section 2: Indexing (10 points)

### Building an index

A retrieval function usually takes in a query document pair, and scores a query against a document.  Our document set is quite small - just a few thousand documents. However, consider a web-scale dataset with a few million documents. In such a scenario, it would become infeasible to score every query and document pair. In such a case, we can build an inverted index. From Wikipedia:

> ... , an inverted index (also referred to as a postings file or inverted file) is a database index storing a mapping from content, such as words or numbers, to its locations in a table, .... The purpose of an inverted index is to allow fast full-text searches, at a cost of increased processing when a document is added to the database. ...


Consider a simple inverted index, which maps from word to document. This can improve the performance of a retrieval system significantly. In this assignment, we consider a *simple* inverted index, which maps a word to a set of documents. In practice, however, more complex indices might be used.  

---

In this assignment we will be using an index created in memory, since our dataset is tiny. To get started, build a simple index that maps simply counts the number of tokens present in a document. This index  is built using a python dictionary.

### *Answer the following questions*:
- What is the time complexity of retrieving a list of documents from a python `dict` object? 
    - *TODO: Answer this!*
    - **Answer:** Retrieving a list from a python dict takes constant time $\theta$(1)  because it uses keys to retrieve values. 
- Consider the case with a 10 million documents. What is the time complexity of retrieval with an inverted index (assuming you can fit the entire index in memory)? (Hint: Consider length of a query $|q|$) 
    - *TODO: Answer this!*
    - **Answer:** Constant time? $\theta$(1)
- For a large enough collection, we cannot store an index in memory. How is this tackled in practice (briefly explain)? Comment on the time complexity. 
    - *TODO: Answer this!*
- Mention a use-case in which a simple index (from word -> doc_id) might not suffice anymore. How would you modify the index to suit this use-case (if you can!)  
    - *TODO: Answer this!*
    
    
Now, implement a function to build an index:

In [48]:
# TODO: Implement this! 10 points
def build_tf_index(documents):
    """
    Build an inverted index (with counts). The output is a dictionary which takes in a token
    and returns a list of (doc_id, count) where 'count' is the count of the 'token' in 'doc_id'
    Input: a list of documents - (doc_id, tokens) 
    Output: An inverted index. [token] -> [(doc_id, token_count)]
    """
    
    invert_index = Counter()
    
    for doc in documents:
        doc_id = doc[0]
        tokens = doc[1]
        
        for token in tokens:
            token_count = (doc_id, tokens.count(token))
            
            if token in invert_index:
                if token_count not in invert_index[token]:
                    invert_index[token].append(token_count)
                    
            else:
                invert_index[token] = [token_count]
    
    return invert_index
 
# Create the 2 indices
tf_index_1 = build_tf_index(doc_repr_1)
tf_index_2 = build_tf_index(doc_repr_2)
pprint(tf_index_1)
# pprint(tf_index_2)

# This function returns the correct index 
def get_index(index_set):
    assert index_set in {1, 2}
    return {
        1: tf_index_1,
        2: tf_index_2
    }[index_set]

# This function returns the correct doc_repr 
def get_doc_repr(index_set):
    assert index_set in {1, 2}
    return {
        1: doc_repr_1,
        2: doc_repr_2
    }[index_set]

# This function correctly pre-processes the text given the index set
def preprocess_query(text, index_set):
    assert index_set in {1, 2}
    if index_set == 1:
        return process_text(text, **config_1)
    elif index_set == 2:
        return process_text(text, **config_2)
    

Counter({'te': [(3204, 1)],
         'santa': [(3204, 1)],
         'monica': [(3204, 1)],
         'assistant': [(3203, 3), (3204, 1)],
         'grad': [(3203, 3)],
         'abd': [(3203, 1)],
         'problemms': [(3203, 1)],
         'radicals': [(3203, 1)],
         'manip': [(3202, 1)],
         'parentheses': [(3202, 1)],
         'waste': [(3201, 1)],
         'problemm': [(3200, 1), (3202, 1)],
         'algem': [(3199, 4)],
         'manipulators': [(3199, 1)],
         'emulators': [(3198, 1)],
         'standards-processing': [(3197, 1)],
         '547-549': [(3197, 1)],
         'telegraph': [(3196, 2)],
         '84-character': [(3196, 1)],
         'alphabetical': [(3196, 1)],
         'dial-type': [(3196, 1)],
         'telex': [(3196, 1)],
         'leased': [(3196, 1)],
         'nondial': [(3196, 1)],
         'interchangeably': [(3196, 1)],
         'reiteration': [(3195, 1)],
         'officers': [(3195, 1)],
         'election': [(3195, 1)],
         'reiterate'

         'confirm': [(2890, 1), (3084, 1)],
         'store-and-forward': [(2890, 1), (3032, 2)],
         'overuse': [(2890, 1)],
         'underuse': [(2890, 1)],
         'hb': [(2889, 9)],
         'revisited': [(2889, 3)],
         'restore': [(2889, 3)],
         'imbalance': [(2889, 1), (2984, 1)],
         '.465': [(2889, 1)],
         '2.78': [(2889, 1)],
         '.214': [(2889, 1)],
         '1.91': [(2889, 1)],
         'methodical': [(2888, 2)],
         'inducing': [(2887, 1), (3100, 2)],
         'error-proneness': [(2887, 1)],
         'student-oriented': [(2887, 1)],
         'error-including': [(2887, 1)],
         '132': [(2887, 1)],
         '1,777': [(2887, 1)],
         '1,4000': [(2887, 1)],
         'high-frequency': [(2887, 1)],
         'classifiable': [(2887, 1)],
         'researchers': [(2887, 1)],
         'correctable': [(2887, 1)],
         'existent': [(2887, 1)],
         'concentrates': [(2886, 1)],
         'assures': [(2886, 1)],
         'left-to-r

         'pyramid': [(2692, 1)],
         'numbering': [(2690, 1), (2853, 1), (2992, 1)],
         'multi-key': [(2688, 1)],
         'drawings': [(2687, 2), (2841, 1), (2967, 2), (3116, 1)],
         'complicates': [(2686, 1), (2896, 1)],
         'universally': [(2684, 1)],
         'stem': [(2684, 1)],
         'prone': [(2683, 1)],
         'calibration': [(2682, 1)],
         'seconds': [(2682, 1)],
         'repacking': [(2681, 5)],
         'beneficial': [(2681, 1), (2919, 1)],
         'degraded': [(2681, 1)],
         'permanently': [(2680, 1)],
         'mountable': [(2680, 1)],
         'mount': [(2680, 1)],
         'issued': [(2680, 1)],
         'bottleneck': [(2680, 1)],
         'mounts': [(2680, 1)],
         'nonresident': [(2680, 1)],
         'qsort': [(2679, 2)],
         'treesort3': [(2679, 1)],
         'a475': [(2678, 1)],
         'r179': [(2677, 1)],
         'r419': [(2676, 1)],
         'fundamentally': [(2674, 1)],
         'non-interactive': [(2674, 1)],


         'imbalances': [(2455, 2)],
         'triangle': [(2455, 1), (2776, 1)],
         'duly': [(2455, 1)],
         'servers': [(2454, 2)],
         'equilibrium': [(2454, 1), (2890, 1)],
         'reinwald': [(2453, 1)],
         'soland': [(2453, 1)],
         'organization-a': [(2452, 1)],
         'elusive': [(2452, 1)],
         'device-related': [(2452, 1)],
         'querying': [(2451, 1)],
         'well-specified': [(2451, 1)],
         'ordinarily': [(2451, 1)],
         'affords': [(2451, 1)],
         'bit-vector': [(2451, 1)],
         'dearth': [(2450, 1)],
         'substantiate': [(2450, 1)],
         'symbol-table': [(2449, 1)],
         'sard': [(2447, 2)],
         'cubatures': [(2447, 2)],
         'kernel': [(2447, 1), (2632, 2), (2869, 3), (3068, 1)],
         'remainders': [(2447, 1)],
         'skew': [(2446, 1)],
         'a455': [(2446, 1)],
         'a456': [(2445, 1)],
         'cliques': [(2444, 1), (3018, 1), (3139, 1)],
         'a457': [(2444, 1)],
 

         'predominators': [(2290, 1)],
         'a430': [(2290, 1)],
         'cellular': [(2289, 6), (2882, 1), (3165, 2)],
         'checkerboard': [(2289, 1)],
         'communicates': [(2289, 1)],
         'challenge': [(2289, 1)],
         'parallelized': [(2289, 1)],
         'wire': [(2289, 1)],
         'noncellular': [(2289, 1)],
         'digitizing': [(2287, 1)],
         'tangency': [(2287, 1)],
         'variable-precision': [(2286, 1), (2555, 4)],
         'low-precision': [(2286, 1)],
         'nonrational': [(2286, 1)],
         'a431': [(2285, 1)],
         'lemke': [(2285, 1)],
         'ax+xb=c': [(2284, 1)],
         'a432': [(2284, 1)],
         'hexagonal': [(2283, 3)],
         'thinning': [(2283, 2)],
         'balance': [(2283, 1), (3042, 1), (3059, 1)],
         'irregularities': [(2283, 1)],
         'thinned': [(2283, 1)],
         'strike': [(2283, 1)],
         'avl': [(2278, 1),
                 (2455, 3),
                 (2889, 1),
                 (296

...

                 (1900, 2),
                 (1901, 5),
                 (1902, 2),
                 (1903, 1),
                 (1904, 1),
                 (1905, 1),
                 (1906, 5),
                 (1908, 5),
                 (1910, 2),
                 (1911, 3),
                 (1912, 1),
                 (1915, 3),
                 (1916, 2),
                 (1924, 3),
                 (1926, 2),
                 (1927, 1),
                 (1928, 10),
                 (1929, 4),
                 (1930, 3),
                 (1931, 5),
                 (1932, 1),
                 (1933, 2),
                 (1934, 1),
                 (1935, 2),
                 (1936, 4),
                 (1937, 4),
                 (1939, 6),
                 (1940, 1),
                 (1945, 3),
                 (1946, 2),
                 (1947, 3),
                 (1948, 3),
                 (1949, 1),
                 (1951, 1),
                 (1954, 1),
                 (1

                (1877, 1),
                (1878, 1),
                (1879, 1),
                (1885, 1),
                (1890, 1),
                (1891, 2),
                (1901, 1),
                (1906, 1),
                (1907, 2),
                (1911, 2),
                (1915, 1),
                (1921, 1),
                (1925, 1),
                (1926, 1),
                (1927, 1),
                (1930, 2),
                (1933, 1),
                (1934, 1),
                (1936, 3),
                (1946, 1),
                (1956, 1),
                (1958, 1),
                (1960, 2),
                (1962, 2),
                (1964, 1),
                (1965, 1),
                (1974, 1),
                (1976, 1),
                (1989, 1),
                (1991, 1),
                (1992, 1),
                (1999, 1),
                (2000, 1),
                (2002, 2),
                (2003, 2),
                (2004, 1),
                (2017, 1),
 

                 (320, 2),
                 (321, 2),
                 (322, 1),
                 (329, 3),
                 (330, 1),
                 (332, 2),
                 (335, 1),
                 (336, 1),
                 (347, 1),
                 (354, 1),
                 (378, 1),
                 (380, 3),
                 (391, 1),
                 (393, 1),
                 (396, 1),
                 (397, 9),
                 (399, 1),
                 (401, 1),
                 (404, 1),
                 (405, 1),
                 (407, 1),
                 (409, 2),
                 (411, 1),
                 (413, 1),
                 (416, 1),
                 (417, 4),
                 (435, 2),
                 (439, 1),
                 (440, 3),
                 (441, 2),
                 (451, 1),
                 (452, 1),
                 (461, 1),
                 (462, 2),
                 (464, 1),
                 (475, 1),
                 (479, 3),
 

                       (2308, 2),
                       (2309, 1),
                       (2312, 1),
                       (2313, 1),
                       (2321, 3),
                       (2322, 1),
                       (2367, 3),
                       (2402, 1),
                       (2495, 1),
                       (2557, 2),
                       (2586, 1),
                       (2607, 1),
                       (2629, 1),
                       (2685, 3),
                       (2756, 1),
                       (2769, 1),
                       (2801, 1),
                       (2893, 3),
                       (2917, 1),
                       (2947, 1),
                       (2948, 1),
                       (2971, 1),
                       (3011, 1),
                       (3024, 1),
                       (3038, 1),
                       (3048, 2),
                       (3054, 1),
                       (3110, 1),
                       (3156, 1),
              

                (2499, 12),
                (2500, 8),
                (2501, 4),
                (2502, 1),
                (2507, 1),
                (2508, 1),
                (2513, 1),
                (2514, 4),
                (2515, 5),
                (2516, 4),
                (2517, 2),
                (2518, 4),
                (2519, 6),
                (2520, 1),
                (2521, 1),
                (2522, 6),
                (2523, 3),
                (2524, 5),
                (2525, 9),
                (2526, 6),
                (2527, 5),
                (2534, 6),
                (2535, 9),
                (2536, 5),
                (2537, 3),
                (2538, 7),
                (2539, 1),
                (2540, 1),
                (2541, 9),
                (2542, 5),
                (2543, 3),
                (2544, 3),
                (2545, 4),
                (2546, 6),
                (2547, 5),
                (2553, 1),
                (2554, 11),

--- 

## Section 3: Retrieval  (80 points)

Now that we have cleaned and processed our dataset, we can start building simple IR systems. 

For now, we consider *simple* IR systems, which involve computing scores from the tokens present in the document/query. More advanced methods are covered in later assignments.

We will implement the following methods in this section:
- TF-IDF
- BM25
- Query Likelihood Models

--- 

### Ranking functions


Probably the simplest IR model is the Bag of Words (BOW) model. Implement a function that scores a query against a document using this model.   

Note that you can use either the count of the token or 'binarize' it i.e set the value equal to 1 if the token appears.   


**Note:** Make sure you use the `get_index` function to retrieve the correct index, and call `preprocess_query` with the correct index!

In [49]:
# TODO: Implement this! 10 points
def bow_search(query, index_set):
    """
        Perform a search over all documents with the given query. 
        Note #1: You have to use the `get_index` function created in the previous cells
        Note #2: You can binarize the counts if you wish to
        Input: 
            query - a (unprocessed) query
            index_set - the index to use
        Output: a list of (document_id, score), sorted in descending relevance to the given query 
    """
    
    # inverted index dict: key=word, value=(doc_id, count)
    invert_index = get_index(index_set)
    
    # process query
    processed_query = preprocess_query(query, index_set)
    
    # make dict with query scores per doc: key=doc_id, value=count of query in doc
    query_scores = {}
    
    for query in processed_query:
        for tup in invert_index[query]:
            if tup[0] in query_scores:
                query_scores[tup[0]] += tup[1]
            else:
                query_scores[tup[0]] = tup[1]
    
    # sort list with query scores in descending order
    bow = sorted([(k, float(v)) for k, v in query_scores.items()], key=lambda tup: tup[1], reverse=True)
    
    return bow  

### *Answer the following questions*: 
- The BOW model is might not be a good choice for use in IR. Why? 
    - *TODO: Answer this!*

In [57]:
####
docs_by_id = dict(docs)
def print_results(docs, len_limit=50):    
    for i, (doc_id, score) in enumerate(docs):
        doc_content = docs_by_id[doc_id].strip().replace("\n", "\\n")[:len_limit] + "..."
        print(f"Rank {i}({score:.2}): {doc_content} ID: {doc_id}")

test_bow = bow_search("allocation algorithms", index_set=2)[:5]
print(f"BOW Results:")
print_results(test_bow)
#### 

BOW Results:
Rank 0(1e+01): The Conversion of Limited-Entry Decision Tables to... ID: 2263
Rank 1(9.0): Efficient Multiprogramming Resource Allocation and... ID: 2499
Rank 2(9.0): Dynamic Memory Allocation in Computer Simulation\n... ID: 2902
Rank 3(9.0): Anomalous Behavior of the Fifty-Percent Rule in Dy... ID: 2911
Rank 4(8.0): Optimizing the Polyphase Sort\nVarious dispersion ... ID: 2146


Before we implement the tf-idf scoring functions, let's first write a function to compute the document frequencies of all words.  

In [51]:
# TODO: Implement this! (5 points)
def compute_df(documents, index_set):
    """
        Compute the document frequency of all terms in the vocabulary
        Input: A list of documents
        Output: A dictionary with {token: document frequency)
    """
    
    # inverted index dict: key=word, value=(doc_id, count)
    invert_index = get_index(index_set)
    
    # dict of word frequency in all docs: key: word, value: word frequency over all docs
    word_freq = {}
    
    for key in invert_index:
        word_freq[key] = len(invert_index[key])
        
    # list of word frequencies in descending order
    sorted_word_freq = sorted(word_freq, key=lambda k: word_freq[k], reverse=True)
    print('Most common words with config {}:\n'.format(index_set), sorted_word_freq[:50], '\n')
    
    return word_freq



# get the document frequencies of each document
df_1 = compute_df([d[1] for d in doc_repr_1], index_set=1)
df_2 = compute_df([d[1] for d in doc_repr_2], index_set=2)

def get_df(index_set):
    assert index_set in {1, 2}
    return {
        1: df_1,
        2: df_2
    }[index_set]

Most common words with config 1:
 ['of', 'a', 'the', '.', 'and', 'for', 'in', ')', 'is', 'to', '(', ',', 'algorithm', 'are', 'an', 'on', 'this', 'with', 'which', 'by', 'be', 'that', 'as', 'computer', 'it', 'system', 'paper', 'can', 'from', 'described', 'method', 'presented', 'program', ']', '[', 'given', 'data', 'use', 'programming', 'or', 'used', 'these', 'systems', 'number', 'has', 'time', 'language', 'such', 'at', 'been'] 

Most common words with config 2:
 ['.', ')', '(', ',', 'algorithm', 'comput', 'program', 'system', 'present', 'method', 'paper', 'problem', ']', '[', 'data', 'languag', 'discuss', 'number', 'process', 'techniqu', 'time', 'oper', 'function', 'general', 'result', 'requir', 'develop', ':', 'applic', 'design', 'structur', "'s", 'inform', 'set', 'implement', "''", '``', 'procedur', 'generat', 'effici', 'storag', 'solut', 'includ', 'base', 'analysi', 'shown', 'perform', ';', 'relat', 'propos'] 



Next, implement a function that computes a tf-idf score given a query.      

In [52]:
# TODO: Implement this! 10 points
def tfidf_search(query, index_set):
    """
        Perform a search over all documents with the given query using tf-idf. 
        Note #1: You have to use the `get_index` (and the `get_df`) function created in the previous cells
        Input: 
            query - a (unprocessed) query
            index_set - the index to use
        Output: a list of (document_id, score), sorted in descending relevance to the given query 
    """
    
    # get inverted index
    invert_index = get_index(index_set)
    
    # get word frequencies
    word_freq = get_df(index_set)
   
    # get corpus (all tokenized docs)
    corpus = get_doc_repr(index_set)
    
    # process query
    processed_query = preprocess_query(query, index_set)
    
    # IDF: log((Total number of sentences (documents))/(Number of sentences (documents) containing the word))
    word_idf_values = {token:np.log(len(corpus)/(1 + word_freq[token])) for token in word_freq}
    
    # TF: (Frequency of the word in the sentence) / (Total number of words in the sentence)
    word_tf_values = {}
    
    for query in processed_query:
        for tup in invert_index[query]:
            tf_value = tup[1] / len(corpus[tup[0] - 1][1])
            if query in word_tf_values:
                word_tf_values[query].append((tup[0], tf_value))
            else:
                word_tf_values[query] = [(tup[0], tf_value)]
    
    tfidf_values = {}
    
    for token in word_tf_values:
        token_idf = word_idf_values[token]
        for tup in word_tf_values[token]:
            doc_id = tup[0]
            token_tf = tup[1]
            if doc_id in tfidf_values:
                tfidf_values[doc_id] += token_idf * token_tf
            else:
                tfidf_values[doc_id] = token_idf * token_tf
    
    tfidf_scores = sorted([(k, v) for k, v in tfidf_values.items()], key=lambda tup: tup[1], reverse=True)
    
    return tfidf_scores

In [58]:
####
test_tfidf = tfidf_search("allocation algorithms", index_set=2)[:5]
print(f"TFIDF Results:")
print_results(test_tfidf)
####

TFIDF Results:
Rank 0(1.1): Techniques for Storage Allocation Algorithms... ID: 270
Rank 1(0.91): Core Allocation Based on Probability... ID: 269
Rank 2(0.91): Experience in Automatic Storage Allocation... ID: 273
Rank 3(0.91): The Case for Dynamic storage Allocation... ID: 279
Rank 4(0.73): Stochastic Evaluation of a Static Storage Allocati... ID: 268


### *Answer the following questions*: 
- It is generally not advisable to use the naive version of tf-idf. Why?
    - *TODO: Answer this!*
- Illustrate with an example why using a sublinear scaling for TF is preferable in some cases.  
    - *TODO: Answer this!*

--- 

### *Answer the following questions*: 
- An alternative way to compute a query<>document score is to vectorize both the query and document (where each dimension corresponds to a token), and compute a score. The score can be computed using a dot product between the query and the document vectors. Why is the cosine similary function a better choice, particularly in IR? 
    - *TODO: Answer this!*
- What is the time complexity of a search if we are using the vector space method mentioned in the previous question? What is the time complexity if we're using an index (assume that it fits in memory)? Assume $N$ is the number of documents and $|q|$ is the length of a query. 
    - *TODO: Answer this!*

--- 

#### Query Likelihood Models

In this section you will implement a simple query likelihood model. 

First, let use implement a naive version of a QL model, assuming a multinomial unigram language model (with a uniform prior over the documents). 

**Note:** Make sure you use the `get_index` function to retrieve the correct index, and call `preprocess_query` with the correct index!

--- 

### *Answer the following questions*: 
- Write down the formula for computing the query likelihood, assuming a multinomial unigram language model. 
    - *TODO: Answer this!*
- What problem does this naive method have? Suggest a simple way to fix it.
    - *TODO: Answer this!*

In [54]:
####
def doc_lengths(documents):
    doc_lengths = {doc_id:len(doc) for (doc_id, doc) in documents}
    return doc_lengths

doc_lengths_1 = doc_lengths(doc_repr_1)
doc_lengths_2 = doc_lengths(doc_repr_2)

def get_doc_lengths(index_set):
    assert index_set in {1, 2}
    return {
        1: doc_lengths_1,
        2: doc_lengths_2
    }[index_set]
####

In [55]:

# TODO: Implement this! 15 points
def naive_ql_search(query, index_set):
    """
        Perform a search over all documents with the given query using a naive QL model. 
        Note #1: You have to use the `get_index` (and get_doc_lengths) function created in the previous cells
        Input: 
            query - a (unprocessed) query
            index_set - the index to use
        Output: a list of (document_id, score), sorted in descending relevance to the given query 
    """
    raise NotImplementedError()

In [56]:
####
test_naiveql = naive_ql_search("report", index_set=1)[:5]
print(f"TFIDF Results:")
print_results(test_naiveql)
####

NotImplementedError: 

Now, let's implement a (slightly more) complex QL model. This model should 'fix' the issue with the previous method. If your model requires hyperparameters, set a reasonable value. 

In [ ]:
# TODO: Implement this! 20 points
def ql_search(query, index_set):
    """
        Perform a search over all documents with the given query using a appropriate QL model. 
        Note #1: You have to use the `get_index` (and get_doc_lengths) function created in the previous cells
        Note #2: You might have to create some variables beforehand and use them in this function
        Input: 
            query - a (unprocessed) query
            index_set - the index to use
        Output: a list of (document_id, score), sorted in descending relevance to the given query 
    """
    raise NotImplementedError()

In [ ]:
#### Test the QL model
test_ql_results = ql_search("report", index_set=1)[:5]
print_results(test_ql_results)
print()
test_ql_results_long = ql_search("report " * 10, index_set=1)[:5]
print_results(test_ql_results_long)
####

### *Answer the following questions*: 
- What happens to the query likelihood for long queries? What is a simple fix for this issue?
    - *TODO: Answer this!*


--- 

#### BM25

In this section, we will implement the widely used and hard to beat BM25 scoring function. 


In [ ]:
# TODO: Implement this! (20 points)
def bm25_search(query, index_set):
    """
        Perform a search over all documents with the given query using BM25. 
        Note #1: You have to use the `get_index` (and `get_doc_lengths`) function created in the previous cells
        Note #2: You might have to create some variables beforehand and use them in this function
        Input: 
            query - a (unprocessed) query
            index_set - the index to use
        Output: a list of (document_id, score), sorted in descending relevance to the given query 
    """
    
    raise NotImplementedError()

In [ ]:
#### Test the BM25 model
test_bm25_results = bm25_search("report", index_set=1)[:5]
print_results(test_bm25_results)
####

### *Answer the following questions*: 
- Briefly explain how the BM25 model improves upon the tf-idf model.
    - *TODO: Answer this!*
    
---

In [ ]:
#### Highlighter function
# class for results
ResultRow = namedtuple("ResultRow", ["doc_id", "snippet", "score"])
# doc_id -> doc
docs_by_id = dict((d[0], d[1]) for d in docs)

def highlight_text(document, query, tol=17):
    import re
    tokens = tokenize(query)
    regex = "|".join(f"(\\b{t}\\b)" for t in tokens)
    regex = re.compile(regex, flags=re.IGNORECASE)
    output = ""
    i = 0
    for m in regex.finditer(document):
        start_idx = max(0, m.start() - tol)
        end_idx = min(len(document), m.end() + tol)
        output += "".join(["...",
                        document[start_idx:m.start()],
                        "<strong>",
                        document[m.start():m.end()],
                        "</strong>",
                        document[m.end():end_idx],
                        "..."])
    return output.replace("\n", " ")


def make_results(query, search_fn, index_set):
    results = []
    for doc_id, score in search_fn(query, index_set):
        highlight = highlight_text(docs_by_id[doc_id], query)
        if len(highlight.strip()) == 0:
            highlight = docs_by_id[doc_id]
        results.append(ResultRow(doc_id, highlight, score))
    return results
####

---
---

The widget below allows you to play with the search functions you've written so far. This can be used, for example, to answer some of the theory questions

In [ ]:
# Set this to the function you want to test
# this function should take in a query (string)
# and return a sorted list of (doc_id, score) 
# with the most relevant document in the first position
search_fn = bm25_search
index_set = 1

text = widgets.Text(description="Search Bar", width=200)
display(text)

def handle_submit(sender):
    print(f"Searching for: '{sender.value}'")
    
    results = make_results(sender.value, search_fn, index_set)
    
    # display only the top 5
    results = results[:5]
    
    body = ""
    for idx, r in enumerate(results):
        body += f"<li>Document #{r.doc_id}({r.score}): {r.snippet}</li>"
    display(HTML(f"<ul>{body}</ul>"))
    

text.on_submit(handle_submit)

## Section 4: Offline Evaluation (45 points)

Before we jump in and implement an algorithm for retrieval, we first have to learn how to evaluate such a system. In particular, we will work with offline evaluation metrics. These metrics are computed on a dataset with known relevance judgements.

Implement the following evaluation metrics. 

1. Precision
2. Recall
3. Mean Average Precision
4. Expected Reciprocal Rank

---
### *Answer the following questions*: 
- What are the main limitations of an offline evaluation?
    - *TODO: Answer this!*

---

Let's take a look at the `qrels.text` file, which contains the ground truth relevance scores. The relevance labels for CACM are binary - either 0 or 1. 


In [ ]:
!head ./datasets/qrels.text

The first column is the `query_id` and the second column is the `document_id`. You can safely ignore the 3rd and 4th columns. Write a function to read in the file: 

In [ ]:
# TODO: Implement this!
def read_qrels(root_folder = "./datasets/"):
    """
        Reads the qrels.text file. 
        Output: A dictionary: query_id -> [list of relevant documents]
    """
    raise NotImplementedError()

qrels = read_qrels()

In [ ]:
####
assert len(qrels) == 52, "There should be 52 queries with relevance judgements"
assert sum(len(j) for j in qrels.values()) == 796, "There should be a total of 796 Relevance Judgements"
####

Now, implement the metrics below. 

**Note:** For a given query `query_id`, you can assume that documents *not* in `qrels[query_id]` are not relevant to `query_id`. 


In [ ]:
# TODO: Implement this! (10 points)
def recall_k(results, relevant_docs, k):
    """
        Compute Recall@K
        Input: 
            results: A sorted list of 2-tuples (document_id, score), with the most relevant document in the first position
            relevant_docs: A set of relevant documents. 
            k: the cut-off
        Output: Recall@K
    """
    raise NotImplementedError()
    
# TODO: Implement this! (10 points)
def precision_k(results, relevant_docs, k):
    """
        Compute Precision@K
        Input: 
            results: A sorted list of 2-tuples (document_id, score), 
                    with the most relevant document in the first position
            relevant_docs: A set of relevant documents. 
            k: the cut-off
        Output: Precision@K
    """
    raise NotImplementedError()

# TODO: Implement this! (10 points)
def average_precision(results, relevant_docs):
    """
        Compute Average Precision (for a single query - the results are 
        averaged across queries to get MAP in the next few cells)
        Hint: You can use the recall_k and precision_k functions here!
        Input: 
            results: A sorted list of 2-tuples (document_id, score), with the most 
                    relevant document in the first position
            relevant_docs: A set of relevant documents. 
        Output: Average Precision
    """
    raise NotImplementedError()


# TODO: Implement this! (15 points)
def err(results, relevant_docs):
    """
        Compute the expected reciprocal rank.
        Hint: https://dl.acm.org/doi/pdf/10.1145/1645953.1646033?download=true
        Input: 
            results: A sorted list of 2-tuples (document_id, score), with the most 
                    relevant document in the first position
            relevant_docs: A set of relevant documents. 
        Output: ERR
        
    """
    raise NotImplementedError()
####

### *Answer the following questions*: 
- What are the main drawbacks of precision & recall?
    - *TODO: Answer this!*
- What problems with Precision@K does Average Precision solve? 
    - *TODO: Answer this!*
- The CACM dataset has *binary* relevance judgements. However, a more suitable way of assigning judgements is to use graded relevance. Mention a metric which might be more suitable for a graded relevance, and breifly explain why. 
    - *TODO: Answer this!*
- Consider a text processing step: stemming. What effect does this have on metrics? (Hint: Try changing the pre-processing config and try it out!)
    - *TODO: Answer this!*

---

Let's define some metrics@k using [partial functions](https://docs.python.org/3/library/functools.html#functools.partial)

In [ ]:
####
recall_at_1 = partial(recall_k, k=1)
recall_at_5 = partial(recall_k, k=5)
recall_at_10 = partial(recall_k, k=10)
precision_at_1 = partial(precision_k, k=1)
precision_at_5 = partial(precision_k, k=5)
precision_at_10 = partial(precision_k, k=10)
####

---

The following function evaluates a `search_fn` using the `metric_fn`. Note that the final number is averaged over all the queries

In [ ]:
####
def evaluate_search_fn(search_fn, metric_fn, index_set):
    # build a dict query_id -> query 
    queries_by_id = dict((q[0], q[1]) for q in queries)
    
    metrics = np.zeros(len(qrels), dtype=np.float32)
    for i, (query_id, relevant_docs) in enumerate(qrels.items()):
        query = queries_by_id[query_id]
        results = search_fn(query, index_set)
        metrics[i] = metric_fn(results, relevant_docs)
    
    return metrics.mean()
####

In [ ]:
index_sets = {1, 2}

list_of_metrics = [
    ("ERR", err),
    ("MAP", average_precision),
    ("Recall@1",recall_at_1),
    ("Recall@5", recall_at_5),
    ("Recall@10", recall_at_10),
    ("Precision@1", precision_at_1),
    ("Precision@5", precision_at_5),
    ("Precision@10", precision_at_10)]

list_of_search_fns = [
    ("NaiveQL", ql_search),
    ("QL", ql_search),
    ("BM25", bm25_search),
    ("BOW", bow_search),
    ("TF-IDF", tfidf_search)
]


results = {}
for index_set in index_sets:
    print(f"Index: {index_set}")
    for search_fn_name, search_fn in list_of_search_fns:
        print(f"\tEvaluating Search Function: {search_fn_name}")
        results[search_fn_name] = {}
        for metric_name, metric_fn in list_of_metrics:
            r = evaluate_search_fn(search_fn, metric_fn, index_set).mean()
            print(f"\t\tMetric: {metric_name}: {r}")
            results[search_fn_name][metric_name] = r
        print()

## Section 5: Results and Analysis (20 points)

The `results` dictionary contains the results for all search functions we implemented. Plot the results in bar charts, with clear labels:

In [ ]:
# TODO: Implement this! (20 points)

Write a summary of what you observe in the results.
You summary should compare results across the 2 indices and the methods being used. State what you expected to see in the results, followed by either supporting evidence *or* justify why the results did not support your expectations.      
*Hint*: You may build upon the answers from the previous sections. 

*TODO: Answer this!*